In [1]:
from kaggle_environments.envs.football.helpers import *

In [2]:
# @human_readable_agent wrapper modifies raw observations 
# provided by the environment:
# https://github.com/google-research/football/blob/master/gfootball/doc/observation.md#raw-observations
# into a form easier to work with by humans.
# Following modifications are applied:
# - Action, PlayerRole and GameMode enums are introduced.
# - 'sticky_actions' are turned into a set of active actions (Action enum)
#    see usage example below.
# - 'game_mode' is turned into GameMode enum.
# - 'designated' field is removed, as it always equals to 'active'
#    when a single player is controlled on the team.
# - 'left_team_roles'/'right_team_roles' are turned into PlayerRole enums.
# - Action enum is to be returned by the agent function.
@human_readable_agent
def agent(obs):
    # Make sure player is running.
    if Action.Sprint not in obs['sticky_actions']:
        return Action.Sprint
    # We always control left team (observations and actions
    # are mirrored appropriately by the environment).
    controlled_player_pos = obs['left_team'][obs['active']]
    # Does the player we control have the ball?
    if obs['ball_owned_player'] == obs['active'] and obs['ball_owned_team'] == 0:
        # Shot if we are 'close' to the goal (based on 'x' coordinate).
        if controlled_player_pos[0] > 0.5:
            return Action.Shot
        # Run towards the goal otherwise.
        return Action.Right
    else:
        # Run towards the ball.
        if obs['ball'][0] > controlled_player_pos[0] + 0.05:
            return Action.Right
        if obs['ball'][0] < controlled_player_pos[0] - 0.05:
            return Action.Left
        if obs['ball'][1] > controlled_player_pos[1] + 0.05:
            return Action.Bottom
        if obs['ball'][1] < controlled_player_pos[1] - 0.05:
            return Action.Top
        # Try to take over the ball if close to the ball.
        return Action.Slide

In [3]:
from kaggle_environments import make

In [4]:
!ls

00_run_random.py  Dockerfile  MANIFEST.in	  setup.py	 Untitled.ipynb
CHANGELOG	  gfootball   README.md		  submission.py
CONTRIBUTING.md   LICENSE     run_docker_test.sh  third_party


In [5]:
env = make("football", configuration={"save_video": True, "scenario_name": "11_vs_11_kaggle", "running_in_notebook": True})
output = env.run(["./submission.py", "do_nothing"])[-1]
print('Left player: reward = %s, status = %s, info = %s' % (output[0]['reward'], output[0]['status'], output[0]['info']))
print('Right player: reward = %s, status = %s, info = %s' % (output[1]['reward'], output[1]['status'], output[1]['info']))
env.render(mode="human", width=800, height=600)

Left player: reward = 1, status = DONE, info = {}
Right player: reward = -1, status = DONE, info = {}


In [6]:
import gym

In [7]:
env = gym.make("GFootball-11_vs_11_kaggle-simple115v2-v0")

In [8]:
obs = env.reset()
obs

array([-1.0110294 , -0.        ,  0.        ,  0.02032536,  0.        ,
       -0.02032536, -0.4266544 , -0.19894461, -0.5055147 , -0.06459399,
       -0.5055147 ,  0.06459298, -0.4266544 ,  0.19894461, -0.18624374,
       -0.10739919, -0.2705252 , -0.        , -0.18624374,  0.10739919,
       -0.01011029, -0.2196155 ,  0.        , -0.        ,  0.        ,
       -0.        ,  0.        , -0.        ,  0.        , -0.        ,
        0.        , -0.        ,  0.        , -0.        ,  0.        ,
       -0.        ,  0.        , -0.        ,  0.        , -0.        ,
        0.        , -0.        ,  0.        , -0.        ,  1.0110294 ,
        0.        ,  0.05055147,  0.        ,  0.01011029, -0.21961753,
        0.4266544 ,  0.19894461,  0.5055147 ,  0.06459399,  0.5055147 ,
       -0.06459298,  0.4266544 , -0.19894461,  0.18624374,  0.10739919,
        0.2705252 ,  0.        ,  0.18624374, -0.10739919,  0.01011029,
        0.2196155 , -0.        ,  0.        , -0.        ,  0.  

In [9]:
obs.shape

(115,)

In [10]:
obs, rew, done, info = env.step(env.action_space.sample())

In [11]:
rew

0.0

In [12]:
done

False

In [13]:
info

{'score_reward': 0}